In [1]:
import numpy as np
from bokeh.plotting import figure, output_notebook, show
import json
import pandas as pd
from shapely.geometry import Polygon

to do:
- pick a route : one that's proper, another that's jumping
- load all the mapped points into a numpy array or similar
- do convex hull
- plot, calculate

In [2]:
def split(u, v, points):
    # return points on left side of UV
    return [p for p in points if np.cross(p - u, v - u) < 0]

def extend(u, v, points):
    if not points:
        return []

    # find furthest point W, and split search to WV, UW
    w = min(points, key=lambda p: np.cross(p - u, v - u))
    p1, p2 = split(w, v, points), split(u, w, points)
    return extend(w, v, p1) + [w] + extend(u, w, p2)

def convex_hull(points):
    # find two hull points, U, V, and split to left and right search
    u = min(points, key=lambda p: p[0])
    v = max(points, key=lambda p: p[0])
    left, right = split(u, v, points), split(v, u, points)
    
    # find convex hull on each side
    return [v] + extend(u, v, left) + [u] + extend(v, u, right) + [v]

In [3]:
route1 = 'payanam/routes/KPL/10AS.json'
route2 = 'payanam/routes/BGD/117L.json'

In [4]:
route1json = json.load(open(route1))
route1json.get('stopsArray0',[])[:4]

[{'stop_name': 'Allwyn Colony',
  'suggested': '158/277D,17.45688,78.43984;17H/219,17.49476,78.35216;gps-logs-ghz,17.50046,78.41603;gps-logs-ghz,17.50033,78.41603;src5,17.50526,78.41143;src5,17.50537,78.41131;src5,17.45672,78.43978',
  'stop_lat': '17.45688',
  'stop_lon': '78.43984',
  'confidence': '0'},
 {'stop_name': 'Vivekananda Nagar',
  'suggested': '219(done),17.49065,78.40744;10K/231K_JDM(done),17.49067,78.40769;219(done),17.48921,78.40894;226(done),17.49102,78.40776;24S/219L,17.48902,78.40845;src5,17.49104,78.40777;src5,17.48921,78.40892;shakti-gtfs,17.49221,78.4051',
  'stop_lat': '17.49065',
  'stop_lon': '78.40744',
  'confidence': '0'},
 {'stop_name': 'Sumithra Nagar',
  'suggested': '10K(done),17.4892,78.40891;219/17H(done),17.48934,78.40854;219/229(done),17.48983,78.41038;226(done),17.48967,78.40808;218(done),17.48991,78.41043;113K/L(done),17.48917,78.40888;219/29(done),17.48981,78.41031;218(done),17.49002,78.41056;219/29(done),17.48997,78.41039;219/229(done),17.48994,7

In [5]:
points1 = []
for stopRow in route1json['stopsArray0']:
    if stopRow.get('stop_lat'):
        points1.append([ float(stopRow.get('stop_lat') ),float(stopRow.get('stop_lon')) ])

for stopRow in route1json['stopsArray1']:
    if stopRow.get('stop_lat'):
        points1.append([ float(stopRow.get('stop_lat') ),float(stopRow.get('stop_lon')) ])

route2json = json.load(open(route2))
points2 = []

for stopRow in route2json['stopsArray0']:
    if stopRow.get('stop_lat'):
        points2.append([ float(stopRow.get('stop_lat') ),float(stopRow.get('stop_lon')) ])

for stopRow in route2json['stopsArray1']:
    if stopRow.get('stop_lat'):
        points2.append([ float(stopRow.get('stop_lat') ),float(stopRow.get('stop_lon')) ])

# np.array(points1)

In [6]:
hull1 = np.array(convex_hull(np.array(points1)))
hull1

array([[17.49067, 78.40769],
       [17.44319, 78.49629],
       [17.43603, 78.50002],
       [17.43442, 78.44867],
       [17.43749, 78.44375],
       [17.48967, 78.4081 ],
       [17.49065, 78.40744],
       [17.49067, 78.40769]])

In [7]:
hull2 = np.array(convex_hull(np.array(points2)))
hull2

array([[17.64059, 78.83373],
       [17.3655 , 78.58858],
       [17.36475, 78.57015],
       [17.37549, 78.55791],
       [17.42915, 78.55204],
       [17.46317, 78.56111],
       [17.46537, 78.56234],
       [17.47066, 78.56676],
       [17.48153, 78.57598],
       [17.64059, 78.83373]])

## Hull for route1 (nice route)

In [8]:
points = np.array(points1)
plot = figure()
plot.scatter(x=points[:, 0], y=points[:, 1])
plot.line(x=hull1[:, 0], y=hull1[:, 1], color='red')
# telling the plotter that we're in a jupyter notebook
output_notebook()
show(plot)

Loading BokehJS ...

In [9]:
# from https://stackoverflow.com/a/45734111/4355695
hullArea1 = Polygon(hull1).area
hullArea1*1000

1.7885733500003287

## Hull for route2 (one stop jumping)

In [10]:
points = np.array(points2)
plot = figure()
plot.scatter(x=points[:, 0], y=points[:, 1])
plot.line(x=hull2[:, 0], y=hull2[:, 1], color='red')
# telling the plotter that we're in a jupyter notebook
output_notebook()
show(plot)

Loading BokehJS ...

In [11]:
hullArea2 = Polygon(hull2).area
hullArea2*1000

18.746537799998443

In [12]:
hullArea1 < hullArea2

True

In [13]:
hullArea2 / hullArea1

10.48127984239226

### so a route with jumpers is giving area 10x larger than a route without jumpers. YAYYY